# Uncapacitated Facility Location Problem

In [1]:
import os
import sys
import time
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

sys.path.append("..")

# Personal modules
from lp.uflp import UFLP
from lp.cflp import CFLP
from lp.telp import TELP

# Plotting modules
import plotly.express as px
import plotly.graph_objects as go

# Linear programming modules
import pulp

# Machine learning modules
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MinMaxScaler

# == Regression
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.svm import SVR
from sklearn.ensemble import RandomForestRegressor

# == Classification
from sklearn.tree import DecisionTreeClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC

# == Clustering
from sklearn.cluster import KMeans
from sklearn_som.som import SOM
from sklearn.cluster import AgglomerativeClustering
from sklearn.cluster import DBSCAN
from sklearn.cluster import OPTICS

# == Neural Networks
from sklearn.neural_network import MLPClassifier
from sklearn.neural_network import MLPRegressor

# == Metrics
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import silhouette_score
from sklearn.metrics import davies_bouldin_score
from sklearn.metrics import precision_score
from sklearn.metrics import classification_report


## Load the data

In [2]:
# import the data and parameters and check the data

data_path = "data/"
start_time = time.time()
# ====Parameters==== #
parameters = pd.read_csv(os.path.join(data_path, "parametros.csv"))
# 1. food_per_person_per_day in tons per day
food_per_person_per_day = float(
    parameters.loc[parameters["parametro"] == "comida_por_persona_en_toneladas"].values[
        0
    ][1]
)
# 2. transport_cost_per_ton_per_km in COP per ton per km
transport_cost_per_ton_per_km = float(
    parameters.loc[
        parameters["parametro"] == "costo_de_transporte_por_tonelada_por_kilomentro"
    ].values[0][1]
)

print(
    f"parameters: \n    food_per_person_per_day: {food_per_person_per_day} \n    transport_cost_per_ton_per_km: {transport_cost_per_ton_per_km}\n"
)
# ====Parameters==== #

# ====importData==== #
# 1. population, from data/municipios_procesado.csv
population = pd.read_csv(
    os.path.join(data_path, "municipios_procesado.csv"), index_col=3
)
# 2. distance, from data/distance_matrix_final.csv
distance = pd.read_csv(
    os.path.join(data_path, "distance_matrix_final.csv"), index_col=0
)
# 3. warehouses, from data/almacenes.csv
warehouses = pd.read_csv(os.path.join(data_path, "almacenes.csv"))
# ====importData==== #

# ====DataProcessing===== #
# fill the nan values in population with the minimum '2024' from the departamento of Chocó for the columns 22:
population.loc[population.isna().any(axis=1), population.columns[18:]] = (
    population[
        population["2024"]
        == population.loc[population["departamento"] == "Chocó"]["2024"].min()
    ]
    .iloc[0, 18:]
    .values
)
# drop the municipalities with nan values in the first column of the distance matrix
distance = distance.dropna(subset=[distance.columns[0]], axis=0)
distance = distance.dropna(subset=[distance.index[0]], axis=1)
# select only the rows in population dpmp that the index is in distance
population = population.loc[distance.index]
# turn the columns of distance into integers
distance.columns = distance.columns.astype(int)
print(
    f"data information: \n    population: {population.shape} \n    distance: {distance.shape} \n    warehouses: \n {warehouses} \n"
)
# ====DataProcessing===== #

# ====DataInformation==== #
# Memory usage of the data
print(f"population memory usage: {population.memory_usage().sum()/1024**2:.2f} MB")
print(f"distance memory usage: {distance.memory_usage().sum()/1024**2:.2f} MB")
print(f"warehouses memory usage: {warehouses.memory_usage().sum()/1024**2:.2f} MB")
# ====DataInformation==== #

# ====DataChecking==== #
# Test to the data if needed
# ====DataChecking==== #
print(f"Elapsed time: {time.time() - start_time:.2f} s")


parameters: 
    food_per_person_per_day: 0.00087617 
    transport_cost_per_ton_per_km: 3364.0

data information: 
    population: (1117, 71) 
    distance: (1117, 1117) 
    warehouses: 
    Type  capacity_ton        cost
0     1          1074   731159925
1     2          2418  1129212606
2     3          9672  4516850424 

population memory usage: 0.61 MB
distance memory usage: 9.56 MB
warehouses memory usage: 0.00 MB
Elapsed time: 0.29 s


## 1. Demand Forecast

we are using the data from the population dataset that has the colombian census information since 1985 to 2035, the current year is 2024 and the last census was performed in 2018, the data was taken on december 2023 from the DANE web page.

First we need to check the current forecast, then use 4 ML algorithms and Deep Learning to create a new model. The Machine Learning algorithms are:
- Multiple Linear Regression.
- Regression Tree.
- Support Vector Machine.
- Random Forest Regression.

Then, we need the Mean Absolute Error (MAE) to compare the models. The best model will be used to forecast the demand for the next 30 years.

In [3]:
# ## 1. Demand Forecast

# 1. Demand Forecast
data = population.copy().iloc[:, 20:]
data = data.transpose()

# Standardize the data
scaler = StandardScaler()
data = pd.DataFrame(scaler.fit_transform(data), index=data.index, columns=data.columns)

# Split the data into train and test sets
train, test = train_test_split(data, test_size=0.2, random_state=0)

# List of models to evaluate
models = {
    "Multiple Linear Regression": LinearRegression(),
    "Regression Tree": DecisionTreeRegressor(
        max_depth=100, min_samples_split=2, min_samples_leaf=1
    ),
    "Support Vector Machine": SVR(C=1.0, kernel="rbf", gamma="scale"),
    "Random Forest Regression 10, 5": RandomForestRegressor(
        n_estimators=10, max_depth=5, min_samples_split=2, min_samples_leaf=1
    ),
    "Random Forest Regression 100, 10": RandomForestRegressor(
        n_estimators=100, max_depth=10, min_samples_split=2, min_samples_leaf=1
    ),
}

best_model = None
best_score = float("-inf")
results = {}

# Iterate over models
for model_name, model in models.items():
    start_time = time.time()
    mean_absolute_errors = []
    mean_squared_errors = []
    r2_scores = []

    # For each column in the data
    for column in data.columns:
        model.fit(train.index.values.reshape(-1, 1), train[column])
        predictions = model.predict(test.index.values.reshape(-1, 1))
        mean_absolute_errors.append(mean_absolute_error(test[column], predictions))
        mean_squared_errors.append(mean_squared_error(test[column], predictions))
        r2_scores.append(r2_score(test[column], predictions))

    avg_r2_score = np.mean(r2_scores)
    results[model_name] = {
        "time": time.time() - start_time,
        "mean_absolute_error": np.mean(mean_absolute_errors),
        "mean_squared_error": np.mean(mean_squared_errors),
        "r2_score": avg_r2_score,
    }

    if avg_r2_score > best_score:
        best_score = avg_r2_score
        best_model = model

# Print results
for model_name, metrics in results.items():
    print(f"{model_name}: {metrics['time']:.2f} s")
    print(f"    Mean Absolute Error: {metrics['mean_absolute_error']}")
    print(f"    Mean Squared Error: {metrics['mean_squared_error']}")
    print(f"    R2 Score: {metrics['r2_score']}")

print(f"\nBest model: {best_model}")

# Create the forecast per municipality since 1985 to 2024+30 years
forecast = pd.DataFrame(index=np.arange(1985, 2024 + 30))
for column in data.columns:
    best_model.fit(data.index.values.reshape(-1, 1), data[column])
    forecast[column] = best_model.predict(np.arange(1985, 2024 + 30).reshape(-1, 1))


# Inverse the standardization
data = pd.DataFrame(
    scaler.inverse_transform(data), index=data.index, columns=data.columns
)
forecast = pd.DataFrame(
    scaler.inverse_transform(forecast), index=forecast.index, columns=forecast.columns
)

# Plot the forecast
fig = go.Figure()
for column in forecast.columns:
    fig.add_trace(
        go.Scatter(
            x=forecast.index,
            y=forecast[column],
            mode="lines+markers",
            name=column,
        )
    )

fig.update_layout(
    title="Population Forecast",
    xaxis_title="Year",
    yaxis_title="Population",
    legend_title="Municipality",
)
fig.show()


Multiple Linear Regression: 1.94 s
    Mean Absolute Error: 0.428457750684778
    Mean Squared Error: 0.3664370666800922
    R2 Score: 0.5860169997999521
Regression Tree: 1.78 s
    Mean Absolute Error: 0.09088492122658727
    Mean Squared Error: 0.03251396694585165
    R2 Score: 0.967284451899873
Support Vector Machine: 1.92 s
    Mean Absolute Error: 0.10992893224062007
    Mean Squared Error: 0.05873704491266884
    R2 Score: 0.9431877181416908
Random Forest Regression 10, 5: 13.46 s
    Mean Absolute Error: 0.07394417628592755
    Mean Squared Error: 0.025129836932726614
    R2 Score: 0.9737444780235093
Random Forest Regression 100, 10: 110.42 s
    Mean Absolute Error: 0.05812191687176698
    Mean Squared Error: 0.02018798265077709
    R2 Score: 0.9803343929199618

Best model: RandomForestRegressor(max_depth=10)


C:\Users\User\AppData\Local\Temp\ipykernel_20472\826159521.py:73: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  forecast[column] = best_model.predict(np.arange(1985, 2024 + 30).reshape(-1, 1))
C:\Users\User\AppData\Local\Temp\ipykernel_20472\826159521.py:73: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  forecast[column] = best_model.predict(np.arange(1985, 2024 + 30).reshape(-1, 1))
C:\Users\User\AppData\Local\Temp\ipykernel_20472\826159521.py:73: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of

## 2. Set facility types

We have 3 types of facilities:
- Type 1: Small facility.
- Type 2: Medium facility.
- Type 3: Large facility.

for each facility type we have the following information:
- Fixed cost.
- Variable cost.

The proposal is to use a mathematical model to determine the number of facilities of each type to minimize the total cost, in order to satisfy the demand. and be able to train a classifier to predict the type of facility that will be needed for the hole country.

### Model

#### Sets
- $I$: Set of municipalities.
- $J$: Types of facilities.

#### Parameters
- $c_{j}$: Capacity of facility type $j$.
- $f_{j}$: Fixed cost of facility type $j$.

- $p_{i}$: Population of municipality $i$.
- $N$: Food Demand per capita in Tonnes.
- $d_{i}$: Demand of municipality $i$ = $p_{i} * N$.
- $r_{i}$: department aggregation of population of municipality $i$.
- $\lambda_{i}$: Multiplier of demand of municipality based on its department population.$

#### Decision Variables
- $x_{ij}$: Number of facilities of type $j$ in municipality $i$.

#### Objective Function
- Minimize the total cost of the facilities.

$$ \text{Min} \sum_{i \in I} \sum_{j \in J} f_{j} * x_{ij} $$

#### Constraints

- Demand constraint: The demand of municipality $i$ must be satisfied.

$$ \sum_{j \in J} x_{ij} * c_{j} \geq d_{i} * \lambda_{i} \quad \forall i \in I $$

- (optional) General capacity:

$$ \sum_{i \in I} \sum_{j \in J} x_{ij} * c_{j} \leq \sum_{i \in I} d_{i} * \lambda_{i} $$

- Non-negativity:

$$ x_{ij} \geq 0 \quad \forall i \in I, \forall j \in J $$

- Integer:

$$ x_{ij} \in \mathbb{Z} \quad \forall i \in I, \forall j \in J $$



In [4]:
# Optimization of the model
p = population.copy()["2024"].sample(frac=0.85, random_state=5)

# ====Parameters==== #
c_j = warehouses["capacity_ton"].values.astype(float)
f_j = warehouses["cost"].values.astype(float)


p_i = p.values.astype(int)
n = food_per_person_per_day * 7
d_i = p_i * n
# Lambda = 2 for the top 32 municipalities, 1 for the rest
lambda_i = np.ones(len(p_i)) * 1.1
lambda_i[np.argsort(p_i)[-32:]] = 1.5
# ====Parameters==== #


# Decision variables: $x_{ij}$
I = range(len(p_i))
J = range(len(c_j))
model = pulp.LpProblem("UFLP", pulp.LpMinimize)
x = pulp.LpVariable.dicts(
    "x", ((i, j) for i in I for j in J), lowBound=0, cat="Integer"
)
y = pulp.LpVariable.dicts("y", ((i, j) for i in I for j in J), cat="Binary")
# Objective function
model += (
    pulp.lpSum(f_j[j] * x[(i, j)] for i in I for j in J),
    "Total cost of the facilities",
)
# Constraints
for i in I:
    model += (
        pulp.lpSum(c_j[j] * x[(i, j)] for j in J) >= d_i[i] * lambda_i[i],
        f"Population demand {i}",
    )
    model += (
        pulp.lpSum(x[(i, j)] for j in J) >= 1,
        f"Facility assignment {i}",
    )
    model += (
        pulp.lpSum(y[(i, j)] for j in J) == 1,
        f"Faacility assignment __ {i}",
    )
    for j in J:
        model += (
            x[(i, j)] <= 100 * y[(i, j)],
            f"Fsacility assignment _ {i} _ {j}",
        )

model += pulp.lpSum(x[(i, j)] * c_j[j] for i in I for j in J) >= pulp.lpSum(
    d_i[i] * lambda_i[i] for i in I
)


# Solve the model
model.solve(
    solver=pulp.PULP_CBC_CMD(
        logPath="__workflowsolution_2.log",
        msg=False,
        timeLimit=5 * 60,
        threads=os.cpu_count(),
    )
)
# Results
print(f"Status: {pulp.LpStatus[model.status]}")
print(f"Objective function: {pulp.value(model.objective)}")
df = pd.DataFrame(
    [[pulp.value(x[(i, j)]) for j in J] for i in I],
    columns=[f"Facility {j}" for j in J],
    index=p.index,
)
df["demand"] = d_i
df["satisfied"] = sum(df[f"Facility {j}"] * c_j[j] for j in J)
df["cost"] = sum(df[f"Facility {j}"] * f_j[j] for j in J)
df["comb"] = df.apply(lambda x: tuple(x[: len(J)]), axis=1)

display(df.comb.unique().size, df.comb.unique())
display(df)


Status: Optimal
Objective function: 811097283420.0


11

array([(1.0, 0.0, 0.0), (0.0, 0.0, 1.0), (0.0, 3.0, 0.0),
       (0.0, 31.0, 0.0), (3.0, 0.0, 0.0), (0.0, 1.0, 0.0),
       (0.0, 6.0, 0.0), (0.0, 9.0, 0.0), (0.0, 2.0, 0.0), (0.0, 5.0, 0.0),
       (0.0, 10.0, 0.0)], dtype=object)

Facility 0  Facility 1  Facility 2      demand  satisfied         cost  \
dpmp                                                                            
25781         1.0         0.0         0.0   43.932040     1074.0  731159925.0   
47318         1.0         0.0         0.0  186.166849     1074.0  731159925.0   
27073         1.0         0.0         0.0   72.635369     1074.0  731159925.0   
25258         1.0         0.0         0.0   33.793877     1074.0  731159925.0   
19142         1.0         0.0         0.0  193.514411     1074.0  731159925.0   
...           ...         ...         ...         ...        ...          ...   
50590         1.0         0.0         0.0   84.834284     1074.0  731159925.0   
47960         1.0         0.0         0.0   67.673618     1074.0  731159925.0   
5147          1.0         0.0         0.0  320.054387     1074.0  731159925.0   
17486         1.0         0.0         0.0  132.746764     1074.0  731159925.0   
85250         1.0         0.0         0.0  251.405591     1074.0  731159925.0   

                  comb  
dpmp                    
25781  (1.0, 0.0, 0.0)  
47318  (1.0, 0.0, 0.0)  
27073  (1.0, 0.0, 0.0)  
25258  (1.0, 0.0, 0.0)  
19142  (1.0, 0.0, 0.0)  
...                ...  
50590  (1.0, 0.0, 0.0)  
47960  (1.0, 0.0, 0.0)  
5147   (1.0, 0.0, 0.0)  
17486  (1.0, 0.0, 0.0)  
85250  (1.0, 0.0, 0.0)  

[949 rows x 7 columns]

## 3. Set facility capacity

We have m types of facilities with different capacities, the proposal is to use the data generated in the previous step to determine the capacity of each facility type in order to satisfy the demand.
Machine Learning algorithms will be used to Classify the type of facility that will be needed for each municipality.
- Decision Tree.
- Linear Discriminant Analysis.
- Logistic Regression.
- Support Vector Machine.

and deep learning to create a new model. The best model will be used to determine the capacity of each facility type.

The objective is to predict 'comb' with the information of 'demand', 'lat', 'lon', and 'dp'.


In [5]:
data = pd.merge(df.copy(), population.copy(), left_index=True, right_index=True)
# drop rows with nan in the 'comb' column
data = data.dropna(subset=["comb"])
# train with a random sample of 80% of the data
# The objective is to predict 'comb' with the information of 'demand', 'lat', 'lon', and 'dp'.
# Convert 'comb' to string and encode it
data["comb"] = data["comb"].apply(lambda x: str(x))
data["comb"] = LabelEncoder().fit_transform(data["comb"])

# Standardize the selected features
data[["demand", "lat", "lon", "dp"]] = StandardScaler().fit_transform(
    data[["demand", "lat", "lon", "dp"]]
)

# Split the data into train and test sets
train_x, test_x, train_y, test_y = train_test_split(
    data[["demand", "lat", "lon", "dp"]], data["comb"], test_size=0.2, random_state=0
)

# Define and evaluate models
models = {
    "Decision Tree": DecisionTreeClassifier(),
    "Linear Discriminant Analysis": LinearDiscriminantAnalysis(),
    "Logistic Regression": LogisticRegression(max_iter=1000),
    "Support Vector Machine": SVC(),
    "Neural Network": MLPClassifier(max_iter=1000, tol=1e-4),
}

best_model = None
best_accuracy = float("-inf")
results = {}
for model_name, model in models.items():

    start_time = time.time()
    model.fit(train_x, train_y)
    predictions = model.predict(test_x)
    accuracy = accuracy_score(test_y, predictions)
    elapsed_time = time.time() - start_time

    results[model_name] = {
        "accuracy": accuracy,
        "confusion_matrix": confusion_matrix(test_y, predictions),
        "classification_report": classification_report(
            test_y, predictions, zero_division=1
        ),
        "time": elapsed_time,
    }

    if accuracy > best_accuracy:
        best_accuracy = accuracy
        best_model = model

# Print results
for model_name, metrics in results.items():
    print(f"{model_name}: {metrics['time']:.2f} s")
    print(f"    Accuracy: {metrics['accuracy']}")
    print(f"    Confusion Matrix: \n {metrics['confusion_matrix']}")
    print(f"    Classification Report: \n {metrics['classification_report']}")

print(f"\nBest model: {best_model}")

# Predict the 'comb' column
data["comb"] = best_model.predict(data[["demand", "lat", "lon", "dp"]])
# Make it to 

display(data)


Decision Tree: 0.01 s
    Accuracy: 1.0
    Confusion Matrix: 
 [[  2   0   0   0   0]
 [  0   1   0   0   0]
 [  0   0   2   0   0]
 [  0   0   0 184   0]
 [  0   0   0   0   1]]
    Classification Report: 
               precision    recall  f1-score   support

           1       1.00      1.00      1.00         2
           3       1.00      1.00      1.00         1
           4       1.00      1.00      1.00         2
           9       1.00      1.00      1.00       184
          10       1.00      1.00      1.00         1

    accuracy                           1.00       190
   macro avg       1.00      1.00      1.00       190
weighted avg       1.00      1.00      1.00       190

Linear Discriminant Analysis: 0.01 s
    Accuracy: 0.9842105263157894
    Confusion Matrix: 
 [[  2   0   0   0   0]
 [  0   1   0   0   0]
 [  0   0   2   0   0]
 [  3   0   0 181   0]
 [  0   0   0   0   1]]
    Classification Report: 
               precision    recall  f1-score   support

        

Facility 0  Facility 1  Facility 2    demand  satisfied         cost  \
dpmp                                                                          
25781         1.0         0.0         0.0 -0.150476     1074.0  731159925.0   
47318         1.0         0.0         0.0 -0.071834     1074.0  731159925.0   
27073         1.0         0.0         0.0 -0.134606     1074.0  731159925.0   
25258         1.0         0.0         0.0 -0.156081     1074.0  731159925.0   
19142         1.0         0.0         0.0 -0.067771     1074.0  731159925.0   
...           ...         ...         ...       ...        ...          ...   
50590         1.0         0.0         0.0 -0.127861     1074.0  731159925.0   
47960         1.0         0.0         0.0 -0.137349     1074.0  731159925.0   
5147          1.0         0.0         0.0  0.002193     1074.0  731159925.0   
17486         1.0         0.0         0.0 -0.101370     1074.0  731159925.0   
85250         1.0         0.0         0.0 -0.035763     1074.0  731159925.0   

       comb                           region  c_digo_dane_del_departamento  \
dpmp                                                                         
25781     9            Región Centro Oriente                            25   
47318     9                    Región Caribe                            47   
27073     9                  Región Pacífico                            27   
25258     9            Región Centro Oriente                            25   
19142     9                  Región Pacífico                            19   
...     ...                              ...                           ...   
50590     9                     Región Llano                            50   
47960     9                    Región Caribe                            47   
5147      9  Región Eje Cafetero - Antioquia                             5   
17486     9  Región Eje Cafetero - Antioquia                            17   
85250     9                     Región Llano                            85   

       departamento  ...     2026     2027     2028     2029     2030  \
dpmp                 ...                                                
25781  Cundinamarca  ...   7563.0   7780.0   7984.0   8163.0   8360.0   
47318     Magdalena  ...  31027.0  31272.0  31561.0  31844.0  32099.0   
27073         Chocó  ...  12076.0  12303.0  12398.0  12503.0  12571.0   
25258  Cundinamarca  ...   5813.0   5973.0   6125.0   6273.0   6431.0   
19142         Cauca  ...  32050.0  32397.0  32631.0  32863.0  33069.0   
...             ...  ...      ...      ...      ...      ...      ...   
50590          Meta  ...  14141.0  14304.0  14428.0  14563.0  14694.0   
47960     Magdalena  ...  11219.0  11275.0  11351.0  11435.0  11506.0   
5147      Antioquia  ...  52854.0  53109.0  53385.0  53650.0  53894.0   
17486        Caldas  ...  21837.0  21932.0  22026.0  22088.0  22158.0   
85250      Casanare  ...  42145.0  42677.0  43201.0  43697.0  44168.0   

          2031     2032     2033     2034     2035  
dpmp                                                
25781   8563.0   8769.0   8966.0   9146.0   9335.0  
47318  32314.0  32572.0  32840.0  33068.0  33264.0  
27073  12790.0  12853.0  12934.0  13006.0  13194.0  
25258   6568.0   6710.0   6860.0   7009.0   7138.0  
19142  33409.0  33611.0  33769.0  33974.0  34278.0  
...        ...      ...      ...      ...      ...  
50590  14829.0  14934.0  15056.0  15146.0  15290.0  
47960  11563.0  11623.0  11677.0  11750.0  11783.0  
5147   54126.0  54350.0  54553.0  54753.0  54942.0  
17486  22232.0  22286.0  22364.0  22436.0  22458.0  
85250  44638.0  45107.0  45560.0  45988.0  46398.0  

[949 rows x 78 columns]

## 4. Propose a k parameter for clustering using Linear Programming

The proposal is to use the data generated in the previous step to determine the number of clusters that will be needed to satisfy the demand. The objective is to minimize the total cost of the facilities.


In [6]:
# Example data (replace with your actual data)
data = population.copy()
data = data.loc[:, ["lat", "lon"]]
data = StandardScaler().fit_transform(data)
data = pd.DataFrame(data, columns=["lat", "lon"], index=population.copy().index)
# Initialize dictionaries to store metrics
metrics = {"inertia": [], "silhouette": [], "davies_bouldin": []}

# Range for the number of clusters
cluster_range = range(2, 20)

# Calculate metrics for each number of clusters
for i in cluster_range:
    model = KMeans(n_clusters=i, random_state=0)
    model.fit(data[["lat", "lon"]])
    metrics["inertia"].append(model.inertia_)
    metrics["silhouette"].append(silhouette_score(data[["lat", "lon"]], model.labels_))
    metrics["davies_bouldin"].append(
        davies_bouldin_score(data[["lat", "lon"]], model.labels_)
    )

# Create interactive plots using Plotly
fig = go.Figure()

# Inertia Plot
fig.add_trace(
    go.Scatter(
        x=list(cluster_range),
        y=metrics["inertia"],
        mode="lines+markers",
        name="Inertia",
        yaxis="y",
    )
)

# Silhouette Plot
fig.add_trace(
    go.Scatter(
        x=list(cluster_range),
        y=metrics["silhouette"],
        mode="lines+markers",
        name="Silhouette Score",
        yaxis="y2",
    )
)

# Davies-Bouldin Plot
fig.add_trace(
    go.Scatter(
        x=list(cluster_range),
        y=metrics["davies_bouldin"],
        mode="lines+markers",
        name="Davies-Bouldin Score",
        yaxis="y2",
    )
)

# Update layout
fig.update_layout(
    title="Clustering Metrics",
    xaxis_title="Number of Clusters",
    yaxis_title="Inertia",
    legend_title="Metric",
    template="plotly_white",
    yaxis=dict(side="left", showgrid=False, zeroline=False, title="Normalized Inertia"),
    yaxis2=dict(
        side="right",
        overlaying="y",
        showgrid=False,
        zeroline=False,
        title="Normalized Score (0-1)",
        title_standoff=10,  # Adjust the distance between the axis title and axis tick labels
    ),
    margin=dict(r=100, t=100),  # Adjust the right and top margins
)

# Show plot
fig.show()


In [7]:
# data = population.copy()
# dist = distance.copy()
# muestra = 0.1
# dist = dist.sample(frac=muestra, random_state=0, axis=0).sample(
#     frac=muestra, random_state=0, axis=1
# )
# # Select the same rows than the distance matrix
# data = data.loc[dist.copy().index]

# # Standardize the data
# dist = MinMaxScaler().fit_transform(dist)
# # dist = dist.values
# fixed_cost = max(dist.flatten())

# model = pulp.LpProblem("UFLP", pulp.LpMinimize)

# max_assignments_per_facility = 0.1 * len(data) * muestra
# # Decision variables
# I = range(len(data))
# J = range(len(data))

# x = pulp.LpVariable.dicts("x", ((i, j) for i in I for j in J), cat="Binary")
# y = pulp.LpVariable.dicts("y", J, cat="Binary")

# # Objective function
# model += (
#     pulp.lpSum(dist[i][j] * x[(i, j)] for i in I for j in J)
#     + fixed_cost * pulp.lpSum(y[j] for j in J),
#     "Total cost",
# )

# # Constraints
# for i in I:
#     model += pulp.lpSum(x[(i, j)] for j in J) == 1, f"Population demand {i}"

# for j in J:
#     for i in I:
#         model += x[(i, j)] <= y[j], f"Facility assignment {i} {j}"
#     model += (
#         pulp.lpSum(x[(i, j)] for i in I) <= max_assignments_per_facility,
#         f"Facility capacity {j}",
#     )

# # Solve the model
# model.solve(
#     solver=pulp.PULP_CBC_CMD(
#         logPath="__workflowsolution_4.log",
#         msg=False,
#         timeLimit=5 * 60,
#         threads=os.cpu_count() - 1,
#     )
# )

# # Results
# print(f"Status: {pulp.LpStatus[model.status]}")
# print(f"Objective function: {pulp.value(model.objective)}")
# print(f"Number of facilities: {pulp.value(pulp.lpSum(y[j] for j in J))}")

# df = pd.DataFrame([[pulp.value(x[(i, j)]) for j in J] for i in I], columns=J, index=I)

# # Turn the results into labels for the clusters
# df["cluster"] = df.idxmax(axis=1)
# display(df["cluster"].unique().size / muestra, df["cluster"].unique())

# # Plot the results
# fig = px.scatter(
#     data,
#     x="lat",
#     y="lon",
#     color=df["cluster"],
#     title="Facilities location",
#     labels={"lat": "Latitude", "lon": "Longitude"},
# )
# fig.show()


## 5. Solve the CFLP inside every cluster

Here, we will use the clusters to find the local optimum to the cflp inside the clusters generated with the following clustering algorithms:

- KMeans
- SOM
- AgglomerativeClustering
- DBSCAN



In [8]:
data = population.copy()
data = data.loc[:, ["lat", "lon"]]
data = StandardScaler().fit_transform(data)
data = pd.DataFrame(data, columns=["lat", "lon"], index=population.copy().index)

# Initialize dictionaries to store metrics
metrics = {
    "model": [],
    "silhouette": [],
    "davies_bouldin": [],
    "n_clusters": [],
    "time": [],
}

# Range for the number of clusters
n_clusters = 6
# models to evaluate
models = {
    "KMeans": KMeans(n_clusters=n_clusters, random_state=0),
    # "SOM": SOM(m=n_clusters, n=1, random_state=0),
    "Agglomerative": AgglomerativeClustering(n_clusters=n_clusters),
    "DBSCAN": DBSCAN(eps=0.3, min_samples=10),
    "OPTICS": OPTICS(min_samples=10),
}

# Calculate metrics for each number of clusters and save the best model
for model_name, model in models.items():
    start_time = time.time()
    model.fit(data)
    data[f"{model_name}_cluster"] = model.labels_
    metrics["time"].append(time.time() - start_time)
    metrics["n_clusters"].append(n_clusters)
    metrics["model"].append(model_name)
    metrics["silhouette"].append(silhouette_score(data, model.labels_))
    metrics["davies_bouldin"].append(davies_bouldin_score(data, model.labels_))

# Create a DataFrame with the results
display(metrics)

# Plot the results
for model_name, model in models.items():
    fig = px.scatter(
        data,
        x="lon",
        y="lat",
        color=f"{model_name}_cluster",
        title=f"{model_name} Clustering",
        labels={"lat": "Latitude", "lon": "Longitude"},
    )
    fig.show()


{'model': ['KMeans', 'Agglomerative', 'DBSCAN', 'OPTICS'],
 'silhouette': [0.6634444890897621,
  0.762159022431619,
  0.7429416092131605,
  0.2727481594847729],
 'davies_bouldin': [0.4748423706736676,
  0.35258621966254045,
  0.8207591047490904,
  0.44548669258881596],
 'n_clusters': [6, 6, 6, 6],
 'time': [0.0070002079010009766,
  0.04899883270263672,
  0.016000747680664062,
  0.852001428604126]}

In [9]:
display(data)
# Size of the clusters for each model
for model_name in models.keys():
    display(data.groupby(f"{model_name}_cluster").size())


lat       lon  KMeans_cluster  Agglomerative_cluster  \
dpmp                                                               
5001   0.245589 -0.574343               1                      1   
5002   0.078276 -0.485713               1                      1   
5004   0.393190 -0.878473               1                      1   
5021   0.288099 -0.280160               1                      1   
5030   0.166041 -0.653241               1                      1   
...         ...       ...             ...                    ...   
17444 -0.115324 -0.252903               1                      1   
52051 -1.566987 -1.532879               3                      5   
76109 -0.651670 -1.503628               5                      2   
47189  2.059002  0.251037               2                      3   
8560   1.906124 -0.086839               2                      3   

       DBSCAN_cluster  OPTICS_cluster  
dpmp                                   
5001                0               0  
5002                0              -1  
5004                0              -1  
5021                0              -1  
5030                0               0  
...               ...             ...  
17444               0              -1  
52051               4               9  
76109               5              -1  
47189               3              -1  
8560                3              -1  

[1117 rows x 6 columns]

KMeans_cluster
0     29
1    305
2    198
3     95
4    368
5    122
dtype: int64

Agglomerative_cluster
0    368
1    305
2    122
3    198
4     29
5     95
dtype: int64

DBSCAN_cluster
-1     55
 0    292
 1    355
 2      9
 3    197
 4     94
 5    115
dtype: int64

OPTICS_cluster
-1     704
 0      20
 1      11
 2      14
 3      38
 4      12
 5      39
 6      13
 7      19
 8      19
 9      21
 10     34
 11     10
 12     16
 13     20
 14     20
 15     23
 16     14
 17     29
 18     12
 19     29
dtype: int64